In [1]:
pwd()

"/home/zyu20/git/BulkLMM.jl/test/notebooks"

In [2]:
cd("..")

In [3]:
Threads.nthreads()

24

In [4]:
include("BXDdata_for_test.jl"); ## Load BXD data used for testing:

In [5]:
using LoopVectorization

In [6]:
include("../src/scan_LiteQTL.jl"); ## Load multithreaded functions to be tested:

In [7]:
include("../src/parallel_helpers.jl");

In [8]:
include("testHelper.jl");

In [9]:
BLAS.set_num_threads(24)

In [10]:
BLAS.get_num_threads()

24

In [11]:
traitID = 1112

1112

In [12]:
@time results_scan_alt = scan_alt(reshape(pheno[:, traitID], :, 1), geno, kinship; reml = false);

  1.537065 seconds (2.54 M allocations: 1.168 GiB, 11.76% gc time)


In [13]:
pve_list = unique(round.(results_scan_alt[3]; digits = 3))

204-element Vector{Float64}:
 0.835
 0.861
 0.847
 0.828
 0.822
 0.84
 0.858
 0.849
 0.838
 0.834
 0.832
 0.826
 0.831
 ⋮
 0.741
 0.787
 0.765
 0.757
 0.768
 0.745
 0.75
 0.763
 0.767
 0.783
 0.939
 0.925

In [14]:
pve_list = collect(1:10) .* 0.1;

In [16]:
@time LODs_bulkscan = bulkscan(pheno, geno, kinship, pve_list);

 12.925918 seconds (1.97 k allocations: 20.237 GiB, 10.28% gc time)


In [17]:
@time LODs_bulkscan = bulkscan(pheno, geno, kinship, [results_scan_alt[3][1]])

  1.221746 seconds (227 allocations: 2.050 GiB, 15.20% gc time, 0.39% compilation time)


7321×35556 Matrix{Float64}:
 0.0685133   0.0774162  0.0712343   …  0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343   …  0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343      0.0469135   0.126384    0.501837
 0.0685133   0.0774162  0.0712343   …  0.0469135   0.126384    0.501837
 0.068516    0.0774187  0.0712363      0.0469141   0.126386    0.501847
 0.156148    0.147156   0.12592        0.0563397   0.1673      0.706861
 ⋮                                  

In [18]:
hcat(results_scan_alt[4], LODs_bulkscan[:, traitID])

7321×2 Matrix{Float64}:
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381039     0.382287
 0.381047     0.382295
 0.576593     0.570371
 ⋮            
 0.000186308  0.000594774
 0.000186308  0.000594774
 0.000186308  0.000594774
 0.0127896    0.0101812
 0.0869155    0.0711951
 0.0869155    0.0711951
 0.428963     0.365588
 0.435515     0.369203
 0.435687     0.369459
 0.425038     0.360271
 0.772675     0.629874
 0.772675     0.629874

In [101]:
sumSqDiff(reshape(results_scan_alt[4], :, 1), reshape(LODs_bulkscan[:, traitID], :, 1))

31.80946174563183

In [19]:
?scan_perms

search: scan_perms scan_perms_distributed



No documentation found.

`scan_perms` is a `Function`.

```
# 1 method for generic function "scan_perms":
[1] scan_perms(y::Matrix{Float64}, g::Matrix{Float64}, K::Matrix{Float64}; nperms, rndseed, reml, original) in Main at /home/zyu20/git/BulkLMM.jl/src/scan.jl:212
```


In [109]:
function scan_perms_temp(y::Array{Float64,2}, g::Array{Float64,2}, K::Array{Float64,2};
              nperms::Int64 = 1024, rndseed::Int64 = 0, 
              reml::Bool = false, original::Bool = true)

    # check the number of traits as this function only works for permutation testing of univariate trait
    if(size(y, 2) != 1)
        error("Can only handle one trait.")
    end

    # n - the sample size
    # p - the number of markers
    (n, p) = size(g)

    # make intercept
    intercept = ones(n, 1)

    # rotate data so errors are uncorrelated
    (y0, X0, lambda0) = rotateData(y, [intercept g], K)


    ## Note: estimate once the variance components from the null model and use for all marker scans
    # fit lmm

    # X0_intercept = @view X0[:, 1] # to compare
    vc = fitlmm(y0, reshape(X0[:, 1], :, 1), lambda0; reml = reml) # vc.b is estimated through weighted least square
    r0 = y0 - X0[:, 1]*vc.b

    # weights proportional to the variances
    sqrtw = sqrt.(makeweights(vc.h2, lambda0))

    # compared runtime of the following with "wls(X0[:, 2:end], X0[:, 1], wts)" ?
    # rescale by weights; now these have the same mean/variance and are independent
    rowMultiply!(r0, sqrtw);
    rowMultiply!(X0, sqrtw);

    
    # after re-weighting X, calling resid on re-weighted X is the same as doing wls on the X after rotation.
    X00 = resid(X0[:, 2:end], reshape(X0[:, 1], :, 1)) # consider not using sub-array, consider @view; in-place changes

    ## random permutations; the first column is the original trait (after transformation)
    rng = MersenneTwister(rndseed);
    ## permute r0 (which is an iid, standard normal distributed N-vector under the null)
    r0perm = shuffleVector(rng, r0[:, 1], nperms; original = original)

    ## Null RSS:
    # By null hypothesis, mean is 0. RSS just becomes the sum of squares of the residuals (r0perm's)
    # (For theoretical derivation of the results, see notebook)
    rss0 = sum(r0perm[:, 1].^2) # a scalar; bc rss0 for every permuted trait is the same under the null (zero mean);
    
    ## make array to hold Alternative RSS's for each permutated trait
    if original
        rss1 = Array{Float64, 2}(undef, nperms+1, p)
    else
        rss1 = Array{Float64, 2}(undef, nperms, p)
    end
    
    ## loop over markers
    for i = 1:p

        ## alternative rss
        @inbounds rss1[:, i] = rss(r0perm, @view X00[:, i]);
        
    end

    lod = -n/(2*log(10)) * log.(rss1 ./ rss0);

    return lod

end

scan_perms_temp (generic function with 1 method)

In [110]:
include("../src/scan_LiteQTL.jl")

bulkscan (generic function with 1 method)

In [111]:
test1 = scan_perms(pheno_y, geno, kinship; nperms = 1, rndseed = 0, reml = false, original = true)[1, :];
test1 = reshape(test1, :, 1);

In [112]:
test2 = scan_null(pheno_y, geno, kinship, reml = false)[3];
test2 = reshape(test2, :, 1);

In [113]:
test3 = scan_perms_temp(pheno_y, geno, kinship; nperms = 1, rndseed = 0, reml = false, original = true)[1, :];
test3 = reshape(test3, :, 1);

In [114]:
(pheno_y0, X0, lambda0) = transform_rotation(pheno_y, geno, kinship);
X0_intercept = reshape(X0[:, 1], :, 1);
X0_covar = X0[:, 2:end];

In [115]:
test4 = scan_lite_univar(pheno_y0[:, 1], X0_intercept, X0_covar, lambda0; reml = false);

In [116]:
test4

7321×1 Matrix{Float64}:
 0.008156051791044849
 0.008156051791044849
 0.008156051791044849
 0.008156051791044849
 0.008156051791044849
 0.008156051791042944
 0.008156051791044849
 0.008156051791044849
 0.008156051791044849
 0.008156051791044849
 0.008156051692277625
 0.008154982152718846
 0.009826183543781484
 ⋮
 0.09161440656773012
 0.09161440624636312
 0.09161440624636502
 0.011249136544344307
 0.008092494360034045
 0.008092494360034045
 0.014799992630069559
 0.028619024387598297
 0.026982655028568586
 0.04459366308898392
 0.01254280302022721
 0.01254280302022721

In [117]:
test5 = scan_alt(pheno_y, geno, kinship; reml = false)[4];
test5 = reshape(test5, :, 1);

In [118]:
hcat(test1, test2, test3, test4, test5)

7321×5 Matrix{Float64}:
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819636  0.0081944   0.00819636  0.00815605  0.00819776
 0.00819528  0.00819333  0.00819528  0.00815498  0.00819668
 0.00987347  0.00987063  0.00987347  0.00982618  0.00987864
 ⋮                                               
 0.0928558   0.0926049   0.0928558   0.0916144   0.0953535
 0.0928558   0.0926049   0.0928558   0.0916144   0.0953535
 0.0928558   0.0926049   0.0

In [121]:
maxSqDiff(test1, test3)

5.491904792216866e-29

In [120]:
maxSqDiff(test2, test3)

99.07294874033582

In [104]:
maxSqDiff(test3, test4)

81.25962819241548

In [107]:
maxSqDiff(test4, test5)

9.153406262625335

In [108]:
sum(test5 .>= test1)

7321

In [146]:
findall(pheno[1, :] .== 5.417)

3-element Vector{Int64}:
  9700
 32600
 35400

In [144]:
pheno[:, 33854]

79-element Vector{Float64}:
 10.104
  9.956
 10.145
 10.272
 10.059
 10.195
 10.02
  9.88
 10.495
 10.182
 10.078
 10.17
 10.054
  ⋮
 10.512
 10.123
  9.873
 10.128
 10.088
 10.331
  9.973
 10.337
 10.064
 10.632
  9.901
 10.257

In [147]:
m - 35400

156

In [36]:
using Plots

In [37]:
histogram(reshape(test1[1, :], :, 1) .- reshape(test2[3], :, 1))